In [17]:

### install packages like numpy, pandas, pillow, matplotlib, pydicom, skimage, scikit-learn, 
##pip install pylibjpeg pylibjpeg-libjpeg pydicom
import pandas as pd
import matplotlib.pyplot as plt
import cv2 as cv
import numpy as np
import os
import random
from sklearn.utils import shuffle
import shutil
import pydicom
from pydicom import dcmread
from skimage.transform import resize
from PIL import Image

In [18]:
magview_path = '/media/careinfolab/CI_Lab/tables/EMBED_OpenData_clinical_reduced.csv'
metadata_path = '/media/careinfolab/CI_Lab/tables/EMBED_OpenData_metadata_reduced.csv'

In [19]:
## Read clinical and metadata rows
magview_path = '/media/careinfolab/CI_Lab/tables/EMBED_OpenData_clinical.csv'
metadata_path = '/media/careinfolab/CI_Lab/tables/EMBED_OpenData_metadata.csv'
df_mag = pd.read_csv(magview_path)

/tmp/ipykernel_262772/2104025010.py:4: DtypeWarning: Columns (28,31,33,48,49,53,54,55,56,57,59,81,84,85,93,111) have mixed types. Specify dtype option on import or set low_memory=False.
  df_mag = pd.read_csv(magview_path)


In [20]:
## Read clinical data and convert date columns into an appropriate style.
df_mag = pd.read_csv(magview_path)
df_mag['study_date_anon'] = pd.to_datetime(df_mag['study_date_anon'], errors='coerce', format= '%Y-%m-%d')
list(df_mag.columns)

/tmp/ipykernel_262772/2091432577.py:2: DtypeWarning: Columns (28,31,33,48,49,53,54,55,56,57,59,81,84,85,93,111) have mixed types. Specify dtype option on import or set low_memory=False.
  df_mag = pd.read_csv(magview_path)


['Unnamed: 0',
 'massshape',
 'massmargin',
 'massdens',
 'calcfind',
 'calcdistri',
 'calcnumber',
 'otherfind',
 'implanfind',
 'consistent',
 'side',
 'size',
 'location',
 'depth',
 'distance',
 'numfind',
 'asses',
 'recc',
 'stable',
 'new',
 'changed',
 'loc_num',
 'tech_init',
 'init',
 'proccode',
 'desc',
 'vtype',
 'tissueden',
 'case',
 'type',
 'technique',
 'biopsite',
 'biop_loc',
 'bcomp',
 'path_loc',
 'diag_out',
 'surgery',
 'lymphsurg',
 'surg_loc',
 'pocomp',
 'ltcomp',
 'bside',
 'path1',
 'path2',
 'path3',
 'path4',
 'path5',
 'path6',
 'path7',
 'path8',
 'path9',
 'path10',
 'concord',
 'hgrade',
 'tnmpt',
 'tnmpn',
 'tnmm',
 'tnmdesc',
 'tnmr',
 'stage',
 'loc',
 'bdepth',
 'bdistance',
 'focality',
 'nfocal',
 'specsize',
 'specsize2',
 'specsize3',
 'dcissize',
 'invsize',
 'superior',
 'inferior',
 'anterior',
 'posterior',
 'medial',
 'lateral',
 'specinteg',
 'specnum',
 'specembed',
 'est',
 'estp',
 'her2',
 'fish',
 'ki67',
 'extracap',
 'methodevl',


In [21]:
## read file metadata files 
df_meta = pd.read_csv(metadata_path)
list(df_meta.columns)

/tmp/ipykernel_262772/3401432801.py:2: DtypeWarning: Columns (115,116,117,118,119,120,130,132,133,134,135,136,138,143,147,148,149) have mixed types. Specify dtype option on import or set low_memory=False.
  df_meta = pd.read_csv(metadata_path)


['Unnamed: 0.2',
 'Unnamed: 0.1',
 'Unnamed: 0',
 'AcquisitionContextSequence',
 'AcquisitionTime',
 '0_AnatomicRegionSequence_CodeMeaning',
 '0_AnatomicRegionSequence_CodeValue',
 '0_AnatomicRegionSequence_CodingSchemeDesignator',
 'AnodeTargetMaterial',
 'BitsAllocated',
 'BitsStored',
 'BodyPartExamined',
 'BodyPartThickness',
 'BreastImplantPresent',
 'BurnedInAnnotation',
 'Columns',
 'CompressionForce',
 'ContentTime',
 'DetectorBinning',
 'DetectorConditionsNominalFlag',
 'DetectorTemperature',
 'DetectorType',
 'DistanceSourceToDetector',
 'DistanceSourceToPatient',
 'EntranceDose',
 'EntranceDoseInmGy',
 'EstimatedRadiographicMagnificationFactor',
 'Exposure',
 'ExposureControlMode',
 'ExposureControlModeDescription',
 'ExposureInuAs',
 'ExposureTime',
 'ExposureTimeInuS',
 'FieldOfViewHorizontalFlip',
 'FieldOfViewOrigin',
 'FieldOfViewRotation',
 'FilterMaterial',
 'FilterThicknessMaximum',
 'FilterThicknessMinimum',
 'FilterType',
 'FocalSpots',
 'Grid',
 'HalfValueLayer',


In [22]:
df_meta.anon_dicom_path[0]

'/mnt/NAS2/mammo/anon_dicom/cohort_1/66685715/1.2.847.113975.3.62.1.55671517.20170931.1/1.2.844.113684.2750828166.1506503583.4742.253/1.2.826.0.1.3680043.8.498.12113965649920234975762962308241977870.dcm'

In [23]:
## Public EMBED dataset has only cohort 1 and 2 

print(df_meta.cohort_num.unique())
print(df_mag.cohort_num.unique())

[1 2]
[1 2]


In [24]:
# Get diagnostic exams with BIRADS 4/5/6
df_mag_diag_pos = df_mag[df_mag.asses.isin(['S','M','K']) & 
                         df_mag.desc.str.contains('diag', case=False)]

# Get and rename relevant columns to prepare for merge with screening exams
df_mag_diag_pos_empi = df_mag_diag_pos[['empi_anon', 
                                        'acc_anon', 
                                        'numfind', 
                                        'bside', 
                                        'study_date_anon', 
                                        'asses']]

df_mag_diag_pos_empi.columns = ['empi_anon', 
                                'acc_anon_diag', 
                                'diag_num', 
                                'diag_side', 
                                'diag_study_date', 
                                'diag_asses']

df_mag_diag_pos_empi

empi_anon     acc_anon_diag  diag_num diag_side diag_study_date  \
22      94981297  5029965028297796         1         L      2013-03-26   
23      94981297  5029965028297796         1         L      2013-03-26   
45      70270720  2327819077874596         1         L      2012-10-05   
121     10774502  5133891846321412         1       NaN      2014-03-19   
222     91015980  2348089114799417         1         L      2013-10-24   
...          ...               ...       ...       ...             ...   
81658   69239061  1663361212874258         3         R      2020-02-27   
81708   76774294  1454137742567162         1         R      2020-01-31   
81717   65816527  5554193707871509         2         R      2020-01-05   
81718   65816527  5554193707871509         1         R      2020-01-05   
81759   41216370  6931964518098386         4         L      2020-04-02   

      diag_asses  
22             S  
23             S  
45             S  
121            S  
222            S  
...          ...  
81658          S  
81708          S  
81717          S  
81718          S  
81759          S  

[3733 rows x 6 columns]

In [25]:
# Get screening exams and left merge on empi_anon(Patient_ID) with df_mag_diag_pos_empi
df_mag_scr = df_mag[df_mag.desc.str.contains('screen', case=False)]
df_mag_scr_pos = df_mag_diag_pos_empi.merge(df_mag_scr, on='empi_anon', how='left')

df_mag_scr_pos

empi_anon     acc_anon_diag  diag_num diag_side diag_study_date  \
0       94981297  5029965028297796         1         L      2013-03-26   
1       94981297  5029965028297796         1         L      2013-03-26   
2       94981297  5029965028297796         1         L      2013-03-26   
3       94981297  5029965028297796         1         L      2013-03-26   
4       94981297  5029965028297796         1         L      2013-03-26   
...          ...               ...       ...       ...             ...   
10532   65816527  5554193707871509         1         R      2020-01-05   
10533   41216370  6931964518098386         4         L      2020-04-02   
10534   41216370  6931964518098386         4         L      2020-04-02   
10535   41216370  6931964518098386         4         L      2020-04-02   
10536   41216370  6931964518098386         4         L      2020-04-02   

      diag_asses  Unnamed: 0 massshape massmargin massdens  ...  \
0              S     21752.0         Q        NaN      NaN  ...   
1              S     33452.0         A        NaN      NaN  ...   
2              S     33453.0         S        NaN      NaN  ...   
3              S     21752.0         Q        NaN      NaN  ...   
4              S     33452.0         A        NaN      NaN  ...   
...          ...         ...       ...        ...      ...  ...   
10532          S     81406.0       NaN        NaN      NaN  ...   
10533          S     70004.0       NaN        NaN      NaN  ...   
10534          S     85701.0       NaN        NaN      NaN  ...   
10535          S     85702.0       NaN        NaN      NaN  ...   
10536          S     85703.0       NaN        NaN      NaN  ...   

      study_date_anon           sdate_anon  procdate_anon  \
0          2017-01-26  2017-01-26 00:00:00     2017-03-30   
1          2018-09-26  2018-09-26 00:00:00            NaN   
2          2018-09-26  2018-09-26 00:00:00            NaN   
3          2017-01-26  2017-01-26 00:00:00     2017-03-30   
4          2018-09-26  2018-09-26 00:00:00            NaN   
...               ...                  ...            ...   
10532      2019-02-04  2019-02-04 00:00:00            NaN   
10533      2017-07-16  2017-07-16 00:00:00            NaN   
10534      2020-03-22  2020-03-22 00:00:00     2020-05-09   
10535      2020-03-22  2020-03-22 00:00:00     2020-05-09   
10536      2020-03-22  2020-03-22 00:00:00            NaN   

                pdate_anon cohort_num path_group path_severity  total_L_find  \
0      2017-04-02 00:00:00        1.0        2.0           2.0           0.0   
1                      NaN        1.0        NaN           NaN           1.0   
2                      NaN        1.0        NaN           NaN           1.0   
3      2017-04-02 00:00:00        1.0        2.0           2.0           0.0   
4                      NaN        1.0        NaN           NaN           1.0   
...                    ...        ...        ...           ...           ...   
10532                  NaN        2.0        NaN           NaN           0.0   
10533                  NaN        2.0        NaN           NaN           0.0   
10534  2020-05-15 00:00:00        2.0        4.0           4.0           1.0   
10535  2020-05-15 00:00:00        2.0        1.0           1.0           1.0   
10536                  NaN        2.0        NaN           NaN           1.0   

      total_R_find first_3_zip  
0              1.0         303  
1              1.0         303  
2              1.0         303  
3              1.0         303  
4              1.0         303  
...            ...         ...  
10532          0.0       303.0  
10533          0.0       300.0  
10534          2.0       300.0  
10535          2.0       300.0  
10536          2.0       300.0  

[10537 rows x 117 columns]

In [26]:
# Keep only screening exams with time diff less than +180 days between diagnosis date and the most recent exam day.
df_mag_scr_pos = df_mag_scr_pos.loc[(df_mag_scr_pos.side == df_mag_scr_pos.diag_side)]
df_mag_scr_pos['study_date_diff'] = df_mag_scr_pos.diag_study_date - df_mag_scr_pos.study_date_anon

df_mag_scr_pos_rel = df_mag_scr_pos.loc[(df_mag_scr_pos.study_date_diff.dt.days >= 0) & 
                                        (df_mag_scr_pos.study_date_diff.dt.days <= 180)]



df_mag_scr_pos_rel

/tmp/ipykernel_262772/1879126741.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_mag_scr_pos['study_date_diff'] = df_mag_scr_pos.diag_study_date - df_mag_scr_pos.study_date_anon


empi_anon     acc_anon_diag  diag_num diag_side diag_study_date  \
6       70270720  2327819077874596         1         L      2012-10-05   
35      63915451  8730500884382410         1         L      2013-03-05   
36      63915451  8730500884382410         1         L      2013-03-05   
40      63915451  8730500884382410         1         L      2013-03-05   
41      63915451  8730500884382410         1         L      2013-03-05   
...          ...               ...       ...       ...             ...   
10498   94251786  3738376430609796         1         R      2020-04-07   
10521   73400780  6925862184233143         1         L      2020-01-21   
10524   85936969  4786838232916669         1         R      2019-09-10   
10525   85936969  4786838232916669         1         R      2019-09-10   
10536   41216370  6931964518098386         4         L      2020-04-02   

      diag_asses  Unnamed: 0 massshape massmargin massdens  ...  \
6              S       240.0       NaN        NaN      NaN  ...   
35             S       560.0       NaN        NaN      NaN  ...   
36             S       561.0       NaN        NaN      NaN  ...   
40             S       560.0       NaN        NaN      NaN  ...   
41             S       561.0       NaN        NaN      NaN  ...   
...          ...         ...       ...        ...      ...  ...   
10498          S     85063.0       NaN        NaN      NaN  ...   
10521          S     85339.0       NaN        NaN      NaN  ...   
10524          K     81239.0         F        NaN      NaN  ...   
10525          K     81240.0         F        NaN      NaN  ...   
10536          S     85703.0       NaN        NaN      NaN  ...   

                sdate_anon procdate_anon           pdate_anon cohort_num  \
6      2012-09-04 00:00:00    2012-10-12  2012-10-12 00:00:00        1.0   
35     2013-02-15 00:00:00    2013-03-07  2013-03-07 00:00:00        1.0   
36     2013-02-15 00:00:00    2013-05-18  2013-05-18 00:00:00        1.0   
40     2013-02-15 00:00:00    2013-03-07  2013-03-07 00:00:00        1.0   
41     2013-02-15 00:00:00    2013-05-18  2013-05-18 00:00:00        1.0   
...                    ...           ...                  ...        ...   
10498  2019-12-02 00:00:00    2020-04-13  2020-04-17 00:00:00        2.0   
10521  2020-01-21 00:00:00    2020-03-01  2020-03-02 00:00:00        2.0   
10524  2019-04-05 00:00:00    2019-10-11  2019-10-15 00:00:00        2.0   
10525  2019-04-05 00:00:00    2019-05-24  1899-09-05 00:00:00        2.0   
10536  2020-03-22 00:00:00           NaN                  NaN        2.0   

      path_group path_severity total_L_find  total_R_find first_3_zip  \
6            4.0           4.0          1.0           0.0       303.0   
35           2.0           2.0          2.0           3.0       303.0   
36           2.0           2.0          2.0           3.0       303.0   
40           2.0           2.0          2.0           3.0       303.0   
41           2.0           2.0          2.0           3.0       303.0   
...          ...           ...          ...           ...         ...   
10498        2.0           2.0          0.0           1.0       300.0   
10521        4.0           4.0          1.0           0.0       300.0   
10524        0.0           0.0          0.0           2.0       305.0   
10525        0.0           0.0          0.0           2.0       305.0   
10536        NaN           NaN          1.0           2.0       300.0   

      study_date_diff  
6             31 days  
35            18 days  
36            18 days  
40            18 days  
41            18 days  
...               ...  
10498        127 days  
10521          0 days  
10524        158 days  
10525        158 days  
10536         11 days  

[2367 rows x 118 columns]

In [27]:
# Get relevant columns from df_meta or merge entire dataset
df_meta_rel = df_meta[['empi_anon', 
                       'acc_anon', 
                       'ViewPosition', 
                       'ImageLateralityFinal', 
                       'FinalImageType', 
                       'png_path', 
                       'num_roi',
                       'anon_dicom_path',
                       'ROI_coords']]

# Merge df_meta_rel with positive exams in magview
df_meta_scr_pos_rel = df_mag_scr_pos_rel.merge(df_meta_rel, 
                                               left_on=['empi_anon', 'acc_anon', 'diag_side'], 
                                               right_on=['empi_anon', 'acc_anon', 'ImageLateralityFinal'], 
                                               how='inner')

# Keep only images with 1 or 2 ROIs
df_meta_scr_pos_rel = df_meta_scr_pos_rel[(df_meta_scr_pos_rel.num_roi == 1) | 
                                          (df_meta_scr_pos_rel.num_roi == 2)]

# Keep only 2D images
df_meta_scr_pos_rel = df_meta_scr_pos_rel[df_meta_scr_pos_rel.FinalImageType == '2D'].reset_index()

print(df_meta_scr_pos_rel.num_roi.value_counts())
print(len(df_meta_scr_pos_rel))

1    1042
2     136
Name: num_roi, dtype: int64
1178


In [28]:

##fixing dicom file paths to the local ones.

def anon_dicom_path_fix(DICOMPathStr):
    return DICOMPathStr.replace('/mnt/NAS2/mammo/anon_dicom', '/media/careinfolab/CI_Lab')

df_meta_scr_pos_rel['anon_dicom_path_local']=df_meta_scr_pos_rel['anon_dicom_path'].apply(anon_dicom_path_fix)

In [29]:

## See whether it displays local paths for dicom files    
df_meta_scr_pos_rel['anon_dicom_path_local'][0]

'/media/careinfolab/CI_Lab/cohort_1/78265628/1.2.846.113971.3.66.1.51529504.20150736.1115118/1.2.840.113683.2750824974.1438237380.2336.34556/1.2.826.0.1.3680043.8.498.10735466440989741668586797439596379519.dcm'

In [ ]:
len(df_meta_scr_pos_rel) ## Display the number of rows it has

In [30]:

def ConvertFromDCMtoPNG(srcPath, dstFolderPath):
    im_dim_x = 800
    im_dim_y = 600

    im = pydicom.dcmread(srcPath)
    print(srcPath + "'s resolution is " + str(im.pixel_array.shape))
    im = im.pixel_array.astype(float)
    ## anti aliasing is true. It is resized into 800 * 600. 
    im = resize(im, (im_dim_x, im_dim_y), anti_aliasing=True)

    ## Rescaled into gray scale image. 
    rescaled_image = (np.maximum(im, 0)/im.max())*65536

    final_image= np.uint16(rescaled_image)
    # Mammograms are converted into 16bit gray scale images    
    print(srcPath + "'s resolution rescaled to " + str(final_image.shape))


    final_image = Image.fromarray(final_image)
    final_image.save(dstFolderPath)

In [31]:

## Mammograms are read from DICOM, resized and color depths are rescaled and stored into seperate folders.
df = df_meta_scr_pos_rel
df = shuffle(df)
all_rois_list = []
all_file_empi_anon_pos = []
save_dir = '/home/careinfolab/FIR_Inchan/breast_simple_comparison/images/800x600/br12_456/'

def CoppFileToDirectory_Pos(Save_Dir):
    for i in range(len(df)):
        if not os.path.exists(Save_Dir):
        # if the demo_folder directory is not present
        # then create it.
            os.makedirs(Save_Dir)
            os.makedirs(Save_Dir + "/pos/")
            os.makedirs(Save_Dir + "/neg/")
        
        img_path = df.anon_dicom_path_local[i]
        empi_anon = df.empi_anon[i]
        filename = os.path.basename(img_path)
        filename = filename +'_' +str(i) + '.png'
        newPath = Save_Dir+'/pos/' + filename
        ConvertFromDCMtoPNG(img_path,newPath)
    
        
        all_file_empi_anon_pos.append([empi_anon, newPath])

CoppFileToDirectory_Pos(save_dir)

/media/careinfolab/CI_Lab/cohort_1/78265628/1.2.846.113971.3.66.1.51529504.20150736.1115118/1.2.840.113683.2750824974.1438237380.2336.34556/1.2.826.0.1.3680043.8.498.10735466440989741668586797439596379519.dcm's resolution is (4096, 3328)
/media/careinfolab/CI_Lab/cohort_1/78265628/1.2.846.113971.3.66.1.51529504.20150736.1115118/1.2.840.113683.2750824974.1438237380.2336.34556/1.2.826.0.1.3680043.8.498.10735466440989741668586797439596379519.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_1/78265628/1.2.846.113971.3.66.1.51529504.20150736.1115118/1.2.842.113685.2750824975.1438237385.2336.34566/1.2.826.0.1.3680043.8.498.11876851440454397415965504044496659551.dcm's resolution is (4096, 3328)
/media/careinfolab/CI_Lab/cohort_1/78265628/1.2.846.113971.3.66.1.51529504.20150736.1115118/1.2.842.113685.2750824975.1438237385.2336.34566/1.2.826.0.1.3680043.8.498.11876851440454397415965504044496659551.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_1

/media/careinfolab/CI_Lab/cohort_1/33448363/1.2.843.113975.3.58.1.51528183.20150734.1093318/1.2.848.113683.2750851772.1438240709.5369.1322/1.2.826.0.1.3680043.8.498.48947913705329060732973369319571877233.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_1/33448363/1.2.843.113975.3.58.1.51528183.20150734.1093318/1.2.848.113683.2750851772.1438240709.5369.1322/1.2.826.0.1.3680043.8.498.48947913705329060732973369319571877233.dcm's resolution is (4096, 3328)
/media/careinfolab/CI_Lab/cohort_1/33448363/1.2.843.113975.3.58.1.51528183.20150734.1093318/1.2.848.113683.2750851772.1438240709.5369.1322/1.2.826.0.1.3680043.8.498.48947913705329060732973369319571877233.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_1/33448363/1.2.843.113975.3.58.1.51528183.20150734.1093318/1.2.848.113683.2750851772.1438240709.5369.1322/1.2.826.0.1.3680043.8.498.48947913705329060732973369319571877233.dcm's resolution is (4096, 3328)
/media/careinfolab/CI_Lab/cohort_1/334

/media/careinfolab/CI_Lab/cohort_1/71018839/1.2.848.113977.3.60.1.51900813.20151017.1124263/1.2.849.113688.2229460969.1170.3622190501.247.1/1.2.826.0.1.3680043.8.498.43123248943775105261826540781686129629.dcm's resolution is (3328, 2560)
/media/careinfolab/CI_Lab/cohort_1/71018839/1.2.848.113977.3.60.1.51900813.20151017.1124263/1.2.849.113688.2229460969.1170.3622190501.247.1/1.2.826.0.1.3680043.8.498.43123248943775105261826540781686129629.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_1/29546625/1.2.842.113972.3.66.1.51936840.20151021.1143625/1.2.844.113625.2.229.207919533134.20344151020153025.10011/1.2.826.0.1.3680043.8.498.11887769598769189362233369157522692723.dcm's resolution is (3062, 2394)
/media/careinfolab/CI_Lab/cohort_1/29546625/1.2.842.113972.3.66.1.51936840.20151021.1143625/1.2.844.113625.2.229.207919533134.20344151020153025.10011/1.2.826.0.1.3680043.8.498.11887769598769189362233369157522692723.dcm's resolution rescaled to (800, 600)
/media/careinf

/media/careinfolab/CI_Lab/cohort_1/67089718/1.2.841.113971.3.64.1.51286149.20150612.1131355/1.2.841.113628.2.72.2198562822.5560150610144448.10008/1.2.826.0.1.3680043.8.498.68275895981981479136728903677960815334.dcm's resolution is (2294, 1914)
/media/careinfolab/CI_Lab/cohort_1/67089718/1.2.841.113971.3.64.1.51286149.20150612.1131355/1.2.841.113628.2.72.2198562822.5560150610144448.10008/1.2.826.0.1.3680043.8.498.68275895981981479136728903677960815334.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_1/67089718/1.2.841.113971.3.64.1.51286149.20150612.1131355/1.2.841.113628.2.72.2198562822.5560150610144448.10008/1.2.826.0.1.3680043.8.498.10209501998299017075644571190714619775.dcm's resolution is (2294, 1914)
/media/careinfolab/CI_Lab/cohort_1/67089718/1.2.841.113971.3.64.1.51286149.20150612.1131355/1.2.841.113628.2.72.2198562822.5560150610144448.10008/1.2.826.0.1.3680043.8.498.10209501998299017075644571190714619775.dcm's resolution rescaled to (800, 600)
/media/car

/media/careinfolab/CI_Lab/cohort_1/36676047/1.2.845.113972.3.59.1.53768287.20161015.1145850/1.2.847.113688.2750824980.1476182151.4311.86005/1.2.826.0.1.3680043.8.498.12459635447318925532412972105139406614.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_1/59992514/1.2.847.113978.3.66.1.53388402.20160804.1150515/1.2.845.113684.2229460963.1011.3647595542.419.1/1.2.826.0.1.3680043.8.498.62119636270978079717035235918801308663.dcm's resolution is (4096, 3328)
/media/careinfolab/CI_Lab/cohort_1/59992514/1.2.847.113978.3.66.1.53388402.20160804.1150515/1.2.845.113684.2229460963.1011.3647595542.419.1/1.2.826.0.1.3680043.8.498.62119636270978079717035235918801308663.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_1/20342368/1.2.841.113972.3.59.1.53760543.20161012.1131058/1.2.845.113684.2230564619.1017.3653648165.83.1/1.2.826.0.1.3680043.8.498.46466915575536134608714448084070269946.dcm's resolution is (4096, 3328)
/media/careinfolab/CI_Lab/cohort_1/

...

/media/careinfolab/CI_Lab/cohort_2/69001424/1.2.846.113970.3.59.1.60737739.20191217.1135759/1.2.841.113688.2750851776.1575875132.3305.73873/1.2.826.0.1.3680043.8.498.12774809018808865853053196850581382365.dcm's resolution is (4096, 3328)
/media/careinfolab/CI_Lab/cohort_2/69001424/1.2.846.113970.3.59.1.60737739.20191217.1135759/1.2.841.113688.2750851776.1575875132.3305.73873/1.2.826.0.1.3680043.8.498.12774809018808865853053196850581382365.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_2/69001424/1.2.846.113970.3.59.1.60737739.20191217.1135759/1.2.847.113682.2750851778.1575875131.3299.73895/1.2.826.0.1.3680043.8.498.48992789959144434670774640721819583212.dcm's resolution is (4096, 3328)
/media/careinfolab/CI_Lab/cohort_2/69001424/1.2.846.113970.3.59.1.60737739.20191217.1135759/1.2.847.113682.2750851778.1575875131.3299.73895/1.2.826.0.1.3680043.8.498.48992789959144434670774640721819583212.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_2

/media/careinfolab/CI_Lab/cohort_2/69001424/1.2.846.113970.3.59.1.60737739.20191217.1135759/1.2.847.113682.2750851778.1575875131.3299.73895/1.2.826.0.1.3680043.8.498.48992789959144434670774640721819583212.dcm's resolution is (4096, 3328)
/media/careinfolab/CI_Lab/cohort_2/69001424/1.2.846.113970.3.59.1.60737739.20191217.1135759/1.2.847.113682.2750851778.1575875131.3299.73895/1.2.826.0.1.3680043.8.498.48992789959144434670774640721819583212.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_2/69001424/1.2.846.113970.3.59.1.60737739.20191217.1135759/1.2.841.113688.2750851776.1575875132.3305.73873/1.2.826.0.1.3680043.8.498.12774809018808865853053196850581382365.dcm's resolution is (4096, 3328)
/media/careinfolab/CI_Lab/cohort_2/69001424/1.2.846.113970.3.59.1.60737739.20191217.1135759/1.2.841.113688.2750851776.1575875132.3305.73873/1.2.826.0.1.3680043.8.498.12774809018808865853053196850581382365.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_2

/media/careinfolab/CI_Lab/cohort_2/69001424/1.2.846.113970.3.59.1.60737739.20191217.1135759/1.2.841.113688.2750851776.1575875132.3305.73873/1.2.826.0.1.3680043.8.498.12774809018808865853053196850581382365.dcm's resolution is (4096, 3328)
/media/careinfolab/CI_Lab/cohort_2/69001424/1.2.846.113970.3.59.1.60737739.20191217.1135759/1.2.841.113688.2750851776.1575875132.3305.73873/1.2.826.0.1.3680043.8.498.12774809018808865853053196850581382365.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_2/69001424/1.2.846.113970.3.59.1.60737739.20191217.1135759/1.2.847.113682.2750851778.1575875131.3299.73895/1.2.826.0.1.3680043.8.498.48992789959144434670774640721819583212.dcm's resolution is (4096, 3328)
/media/careinfolab/CI_Lab/cohort_2/69001424/1.2.846.113970.3.59.1.60737739.20191217.1135759/1.2.847.113682.2750851778.1575875131.3299.73895/1.2.826.0.1.3680043.8.498.48992789959144434670774640721819583212.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_2

/media/careinfolab/CI_Lab/cohort_2/43298560/1.2.844.113970.3.57.1.61235376.20200220.1153419/1.2.849.113684.2750851751.1582007324.4106.72900/1.2.826.0.1.3680043.8.498.88081892021299926011529163579412916104.dcm's resolution is (3328, 2560)
/media/careinfolab/CI_Lab/cohort_2/43298560/1.2.844.113970.3.57.1.61235376.20200220.1153419/1.2.849.113684.2750851751.1582007324.4106.72900/1.2.826.0.1.3680043.8.498.88081892021299926011529163579412916104.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_2/43298560/1.2.844.113970.3.57.1.61235376.20200220.1153419/1.2.842.113688.2750851752.1582007329.4109.72947/1.2.826.0.1.3680043.8.498.23647936032967435617327374079797338440.dcm's resolution is (3328, 2560)
/media/careinfolab/CI_Lab/cohort_2/43298560/1.2.844.113970.3.57.1.61235376.20200220.1153419/1.2.842.113688.2750851752.1582007329.4109.72947/1.2.826.0.1.3680043.8.498.23647936032967435617327374079797338440.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_2

/media/careinfolab/CI_Lab/cohort_2/36850234/1.2.840.113973.3.57.1.61276852.20200226.1120446/1.2.843.113682.2750851781.1582527913.5080.209086/1.2.826.0.1.3680043.8.498.90298768997905654875830036897165680828.dcm's resolution is (3328, 2560)
/media/careinfolab/CI_Lab/cohort_2/36850234/1.2.840.113973.3.57.1.61276852.20200226.1120446/1.2.843.113682.2750851781.1582527913.5080.209086/1.2.826.0.1.3680043.8.498.90298768997905654875830036897165680828.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_2/36850234/1.2.840.113973.3.57.1.61276852.20200226.1120446/1.2.848.113686.2750851776.1582527918.5081.209041/1.2.826.0.1.3680043.8.498.12413726991785673285368564768542071984.dcm's resolution is (3328, 2560)
/media/careinfolab/CI_Lab/cohort_2/36850234/1.2.840.113973.3.57.1.61276852.20200226.1120446/1.2.848.113686.2750851776.1582527918.5081.209041/1.2.826.0.1.3680043.8.498.12413726991785673285368564768542071984.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/coho

In [32]:
## Create a seperate metadata file for converted malignant mammogram images
pos_df = pd.DataFrame(all_file_empi_anon_pos, columns=['empi_anon', 'file_path'])
pos_df.to_csv('/home/careinfolab/FIR_Inchan/breast_simple_comparison/images/800x600/br12_456/pos_empi_path.csv')

In [33]:
# Get screening exams with BIRADS 1/2
df_mag_scr_neg = df_mag[df_mag.desc.str.contains('screen', case=False) & 
                        df_mag.asses.isin(['N','B'])]

# Exclude patients that are included in the positive set
df_mag_scr_neg_rel = df_mag_scr_neg[~df_mag_scr_neg.empi_anon.isin(df_meta_scr_pos_rel.empi_anon)].sort_index()

# Merge df_meta_rel with negative screening exams in magview
df_meta_scr_neg_rel = pd.merge(df_mag_scr_neg_rel, 
                               df_meta_rel,
                               left_on=['empi_anon', 'acc_anon', 'side'], 
                               right_on=['empi_anon', 'acc_anon', 'ImageLateralityFinal'], 
                               how='inner')

# Keep only 2D images
df_meta_scr_neg_rel = df_meta_scr_neg_rel[df_meta_scr_neg_rel.FinalImageType == '2D'].reset_index()

df_meta_scr_neg_rel

index  Unnamed: 0 massshape massmargin massdens calcfind calcdistri  \
0          0         167       NaN        NaN      NaN        Q        NaN   
1          1         167       NaN        NaN      NaN        Q        NaN   
2          2         204       NaN        NaN      NaN      NaN        NaN   
3          3         204       NaN        NaN      NaN      NaN        NaN   
4          4         204       NaN        NaN      NaN      NaN        NaN   
...      ...         ...       ...        ...      ...      ...        ...   
17015  22875       85694       NaN        NaN      NaN      NaN        NaN   
17016  22876       85694       NaN        NaN      NaN      NaN        NaN   
17017  22879       85713       NaN        NaN      NaN      NaN        NaN   
17018  22880       85713       NaN        NaN      NaN      NaN        NaN   
17019  22881       85713       NaN        NaN      NaN      NaN        NaN   

       calcnumber otherfind implanfind  ... total_L_find total_R_find  \
0               0       NaN        NaN  ...          1.0          0.0   
1               0       NaN        NaN  ...          1.0          0.0   
2               0         U        NaN  ...          0.0          1.0   
3               0         U        NaN  ...          0.0          1.0   
4               0         U        NaN  ...          0.0          1.0   
...           ...       ...        ...  ...          ...          ...   
17015           0       NaN        NaN  ...          0.0          1.0   
17016           0       NaN        NaN  ...          0.0          1.0   
17017           0         U        NaN  ...          2.0          1.0   
17018           0         U        NaN  ...          2.0          1.0   
17019           0         U        NaN  ...          2.0          1.0   

       first_3_zip ViewPosition ImageLateralityFinal  FinalImageType  \
0            300.0          MLO                    L              2D   
1            300.0           CC                    L              2D   
2            300.0          MLO                    R              2D   
3            300.0          MLO                    R              2D   
4            300.0           CC                    R              2D   
...            ...          ...                  ...             ...   
17015        300.0           CC                    R              2D   
17016        300.0          MLO                    R              2D   
17017        301.0          MLO                    L              2D   
17018        301.0           CC                    L              2D   
17019        301.0           CC                    L              2D   

                                                png_path num_roi  \
0      /mnt/PACS_NAS1/mammo/png/cohort_1/extracted-im...       0   
1      /mnt/PACS_NAS1/mammo/png/cohort_1/extracted-im...       0   
2      /mnt/PACS_NAS1/mammo/png/cohort_1/extracted-im...       0   
3      /mnt/PACS_NAS1/mammo/png/cohort_1/extracted-im...       0   
4      /mnt/PACS_NAS1/mammo/png/cohort_1/extracted-im...       0   
...                                                  ...     ...   
17015  /mnt/PACS_NAS1/mammo/png/cohort_2/extracted-im...       0   
17016  /mnt/PACS_NAS1/mammo/png/cohort_2/extracted-im...       0   
17017  /mnt/PACS_NAS1/mammo/png/cohort_2/extracted-im...       0   
17018  /mnt/PACS_NAS1/mammo/png/cohort_2/extracted-im...       0   
17019  /mnt/PACS_NAS1/mammo/png/cohort_2/extracted-im...       0   

                                         anon_dicom_path  ROI_coords  
0      /mnt/NAS2/mammo/anon_dicom/cohort_1/69002034/1...          ()  
1      /mnt/NAS2/mammo/anon_dicom/cohort_1/69002034/1...          ()  
2      /mnt/NAS2/mammo/anon_dicom/cohort_1/65261061/1...          ()  
3      /mnt/NAS2/mammo/anon_dicom/cohort_1/65261061/1...          ()  
4      /mnt/NAS2/mammo/anon_dicom/cohort_1/65261061/1...          ()  
...                                                  ...         ...  
17015  /mnt/NA

In [34]:
df_meta_scr_neg_rel['anon_dicom_path_local']=df_meta_scr_neg_rel['anon_dicom_path'].apply(anon_dicom_path_fix)

In [35]:
## See whether it displays local paths for dicom files    
df_meta_scr_neg_rel['anon_dicom_path_local'][0]

'/media/careinfolab/CI_Lab/cohort_1/69002034/1.2.843.113978.3.63.1.47894008.20130618.1102517/1.2.847.113624.2.71.2198562823.1128130613111558.10003/1.2.826.0.1.3680043.8.498.46194445171127345582379108659041212245.dcm'

In [36]:
len(df_meta_scr_neg_rel) # see the number of rows it has

17020

In [37]:
## Read DICOM files and store them into 16Bit pngs with 800 x 600 resolutions.
df = df_meta_scr_neg_rel
df = shuffle(df)
all_rois_list = []
all_file_empi_anon_neg = []
save_dir = '/home/careinfolab/FIR_Inchan/breast_simple_comparison/images/800x600/br12_456/'

def CoppFileToDirectory_Neg(Save_Dir):
    for i in range(len(df)):
        if not os.path.exists(Save_Dir):
        # if the demo_folder directory is not present
        # then create it.
            os.makedirs(Save_Dir)
            os.makedirs(Save_Dir + "/pos/")
            os.makedirs(Save_Dir + "/neg/")
        
        img_path = df.anon_dicom_path_local[i]
        empi_anon = df.empi_anon[i]
        filename = os.path.basename(img_path)
        filename = filename +'_' +str(i) + '.png'
        newPath = Save_Dir+'/neg/' + filename
        ConvertFromDCMtoPNG(img_path,newPath)
    
        
        all_file_empi_anon_neg.append([empi_anon, newPath])

CoppFileToDirectory_Neg(save_dir)

/media/careinfolab/CI_Lab/cohort_1/69002034/1.2.843.113978.3.63.1.47894008.20130618.1102517/1.2.847.113624.2.71.2198562823.1128130613111558.10003/1.2.826.0.1.3680043.8.498.46194445171127345582379108659041212245.dcm's resolution is (2294, 1914)
/media/careinfolab/CI_Lab/cohort_1/69002034/1.2.843.113978.3.63.1.47894008.20130618.1102517/1.2.847.113624.2.71.2198562823.1128130613111558.10003/1.2.826.0.1.3680043.8.498.46194445171127345582379108659041212245.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_1/69002034/1.2.843.113978.3.63.1.47894008.20130618.1102517/1.2.847.113624.2.71.2198562823.1128130613111558.10003/1.2.826.0.1.3680043.8.498.75496604416711804050840880908434765792.dcm's resolution is (2294, 1914)
/media/careinfolab/CI_Lab/cohort_1/69002034/1.2.843.113978.3.63.1.47894008.20130618.1102517/1.2.847.113624.2.71.2198562823.1128130613111558.10003/1.2.826.0.1.3680043.8.498.75496604416711804050840880908434765792.dcm's resolution rescaled to (800, 600)
/media/car

/media/careinfolab/CI_Lab/cohort_1/67011262/1.2.847.113976.3.58.1.47727410.20130507.1091659/1.2.843.113681.2750824976.1367821956.4934.698/1.2.826.0.1.3680043.8.498.62628465975027434908335042367102887897.dcm's resolution is (3328, 2560)
/media/careinfolab/CI_Lab/cohort_1/67011262/1.2.847.113976.3.58.1.47727410.20130507.1091659/1.2.843.113681.2750824976.1367821956.4934.698/1.2.826.0.1.3680043.8.498.62628465975027434908335042367102887897.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_1/28017834/1.2.842.113973.3.66.1.48467682.20131021.1153920/1.2.843.113689.2750851775.1382079708.5157.2721/1.2.826.0.1.3680043.8.498.13152885337731588332816475694447047422.dcm's resolution is (3328, 2560)
/media/careinfolab/CI_Lab/cohort_1/28017834/1.2.842.113973.3.66.1.48467682.20131021.1153920/1.2.843.113689.2750851775.1382079708.5157.2721/1.2.826.0.1.3680043.8.498.13152885337731588332816475694447047422.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_1/28017

/media/careinfolab/CI_Lab/cohort_1/21198109/1.2.849.113979.3.58.1.47300063.20130116.1101843/1.2.842.113685.2750824467.1357713195.3221.666/1.2.826.0.1.3680043.8.498.40592822291471946929748107160657968254.dcm's resolution is (3328, 2560)
/media/careinfolab/CI_Lab/cohort_1/21198109/1.2.849.113979.3.58.1.47300063.20130116.1101843/1.2.842.113685.2750824467.1357713195.3221.666/1.2.826.0.1.3680043.8.498.40592822291471946929748107160657968254.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_1/21198109/1.2.849.113979.3.58.1.47300063.20130116.1101843/1.2.841.113688.2750824470.1357713194.3224.635/1.2.826.0.1.3680043.8.498.98255618863452128168866833256359352827.dcm's resolution is (3328, 2560)
/media/careinfolab/CI_Lab/cohort_1/21198109/1.2.849.113979.3.58.1.47300063.20130116.1101843/1.2.841.113688.2750824470.1357713194.3224.635/1.2.826.0.1.3680043.8.498.98255618863452128168866833256359352827.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_1/2119810

/media/careinfolab/CI_Lab/cohort_1/51793812/1.2.848.113972.3.58.1.47857315.20130607.1/1.2.849.113689.2750824506.1370327327.4998.1190/1.2.826.0.1.3680043.8.498.13075838499228836906962642544436660847.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_1/51793812/1.2.848.113972.3.58.1.47857315.20130607.1/1.2.844.113688.2750824500.1370327325.5004.1116/1.2.826.0.1.3680043.8.498.76221852083235484402754065637179639848.dcm's resolution is (4096, 3328)
/media/careinfolab/CI_Lab/cohort_1/51793812/1.2.848.113972.3.58.1.47857315.20130607.1/1.2.844.113688.2750824500.1370327325.5004.1116/1.2.826.0.1.3680043.8.498.76221852083235484402754065637179639848.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_1/51793812/1.2.848.113972.3.58.1.47857315.20130607.1/1.2.847.113685.2750824505.1370327325.4999.1183/1.2.826.0.1.3680043.8.498.77682618826643923697172187442221350289.dcm's resolution is (4096, 3328)
/media/careinfolab/CI_Lab/cohort_1/51793812/1.2.848.113972.3.5

/media/careinfolab/CI_Lab/cohort_1/77089078/1.2.840.113970.3.57.1.48512322.20131029.1092248/1.2.841.113689.2750824977.1383028413.4634.65072/1.2.826.0.1.3680043.8.498.65402528789975993631849061166075583516.dcm's resolution is (4096, 3328)
/media/careinfolab/CI_Lab/cohort_1/77089078/1.2.840.113970.3.57.1.48512322.20131029.1092248/1.2.841.113689.2750824977.1383028413.4634.65072/1.2.826.0.1.3680043.8.498.65402528789975993631849061166075583516.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_1/10873564/1.2.847.113971.3.60.1.48300853.20130920.1140228/1.2.845.113627.2.70.2198562816.6125130912142602.10010/1.2.826.0.1.3680043.8.498.30753791017900676970855992582055447198.dcm's resolution is (2294, 1914)
/media/careinfolab/CI_Lab/cohort_1/10873564/1.2.847.113971.3.60.1.48300853.20130920.1140228/1.2.845.113627.2.70.2198562816.6125130912142602.10010/1.2.826.0.1.3680043.8.498.30753791017900676970855992582055447198.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_

...

/media/careinfolab/CI_Lab/cohort_2/25841130/1.2.848.113976.3.63.1.60901957.20200112.1080252/1.2.845.113687.2750824543.1578032344.4040.57764/1.2.826.0.1.3680043.8.498.43982994216602708566621150766927406668.dcm's resolution is (4096, 3328)
/media/careinfolab/CI_Lab/cohort_2/25841130/1.2.848.113976.3.63.1.60901957.20200112.1080252/1.2.845.113687.2750824543.1578032344.4040.57764/1.2.826.0.1.3680043.8.498.43982994216602708566621150766927406668.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_2/25841130/1.2.848.113976.3.63.1.60901957.20200112.1080252/1.2.842.113684.2750824546.1578032343.4035.57748/1.2.826.0.1.3680043.8.498.10558907203641153459825359730790003757.dcm's resolution is (4096, 3328)
/media/careinfolab/CI_Lab/cohort_2/25841130/1.2.848.113976.3.63.1.60901957.20200112.1080252/1.2.842.113684.2750824546.1578032343.4035.57748/1.2.826.0.1.3680043.8.498.10558907203641153459825359730790003757.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_2

/media/careinfolab/CI_Lab/cohort_2/38492833/1.2.845.113972.3.62.1.60919343.20200110.1090511/1.2.848.113623.2.409.1196017357155224.12959200106094036.10016/1.2.826.0.1.3680043.8.498.24942115643658288836113635468998003512.dcm's resolution is (2294, 1914)
/media/careinfolab/CI_Lab/cohort_2/38492833/1.2.845.113972.3.62.1.60919343.20200110.1090511/1.2.848.113623.2.409.1196017357155224.12959200106094036.10016/1.2.826.0.1.3680043.8.498.24942115643658288836113635468998003512.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_2/90809712/1.2.841.113979.3.65.1.62038957.20200727.1100945/1.2.849.113683.2750851757.1595400963.4239.46223/1.2.826.0.1.3680043.8.498.10268326526596592624450532580277795546.dcm's resolution is (3328, 2560)
/media/careinfolab/CI_Lab/cohort_2/90809712/1.2.841.113979.3.65.1.62038957.20200727.1100945/1.2.849.113683.2750851757.1595400963.4239.46223/1.2.826.0.1.3680043.8.498.10268326526596592624450532580277795546.dcm's resolution rescaled to (800, 600)
/media

/media/careinfolab/CI_Lab/cohort_2/51728251/1.2.840.113970.3.64.1.61003807.20200125.1074724/1.2.846.113683.2750824974.1579241193.4298.8690/1.2.826.0.1.3680043.8.498.91891945250364190112732498627192700407.dcm's resolution is (3328, 2560)
/media/careinfolab/CI_Lab/cohort_2/51728251/1.2.840.113970.3.64.1.61003807.20200125.1074724/1.2.846.113683.2750824974.1579241193.4298.8690/1.2.826.0.1.3680043.8.498.91891945250364190112732498627192700407.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_2/51728251/1.2.840.113970.3.64.1.61003807.20200125.1074724/1.2.848.113684.2750824979.1579241191.4298.8497/1.2.826.0.1.3680043.8.498.69863969715325686544934867783531365343.dcm's resolution is (3328, 2560)
/media/careinfolab/CI_Lab/cohort_2/51728251/1.2.840.113970.3.64.1.61003807.20200125.1074724/1.2.848.113684.2750824979.1579241191.4298.8497/1.2.826.0.1.3680043.8.498.69863969715325686544934867783531365343.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_2/517

/media/careinfolab/CI_Lab/cohort_2/22096784/1.2.840.113978.3.64.1.62125425.20200805.1152712/1.2.840.113684.2750824972.1596529207.862.56234/1.2.826.0.1.3680043.8.498.83810414734347126554848969443154455711.dcm's resolution is (4096, 3328)
/media/careinfolab/CI_Lab/cohort_2/22096784/1.2.840.113978.3.64.1.62125425.20200805.1152712/1.2.840.113684.2750824972.1596529207.862.56234/1.2.826.0.1.3680043.8.498.83810414734347126554848969443154455711.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_2/22096784/1.2.840.113978.3.64.1.62125425.20200805.1152712/1.2.849.113690.2750824980.1596529213.864.56125/1.2.826.0.1.3680043.8.498.21502497352671595401439633623607432503.dcm's resolution is (4096, 3328)
/media/careinfolab/CI_Lab/cohort_2/22096784/1.2.840.113978.3.64.1.62125425.20200805.1152712/1.2.849.113690.2750824980.1596529213.864.56125/1.2.826.0.1.3680043.8.498.21502497352671595401439633623607432503.dcm's resolution rescaled to (800, 600)
/media/careinfolab/CI_Lab/cohort_2/220

/media/careinfolab/CI_Lab/cohort_2/60824707/1.2.845.113979.3.64.1.61821801.20200620.1101029/1.2.841.113685.2750824977.1592296746.4266.15561/1.2.826.0.1.3680043.8.498.71065897153964749499202415905239872313.dcm's resolution is (3328, 2560)
/media/careinfolab/CI_Lab/cohort_2/60824707/1.2.845.113979.3.64.1.61821801.20200620.1101029/1.2.841.113685.2750824977.1592296746.4266.15561/1.2.826.0.1.3680043.8.498.71065897153964749499202415905239872313.dcm's resolution rescaled to (800, 600)


In [39]:
# create a metadata file for benign mammograms.
neg_df = pd.DataFrame(all_file_empi_anon_neg, columns=['empi_anon', 'file_path'])
neg_df.to_csv('/home/careinfolab/FIR_Inchan/breast_simple_comparison/images/800x600/br12_456/neg_empi_path.csv')